In [2]:
!nvidia-smi

Sat Mar  8 20:52:02 2025       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 525.116.04   Driver Version: 525.116.04   CUDA Version: 12.0     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA GeForce ...  On   | 00000000:3D:00.0 Off |                  N/A |
| 30%   25C    P8     5W / 250W |   6209MiB / 11264MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [4]:
ROOT_DIR = "/data/GraspLLM_open/Multi-GraspSet"
import os
import sys
sys.path.append(ROOT_DIR)
os.chdir(ROOT_DIR)


from utils.hand_model import HandModel
from utils.panda_gripper import PandaGripper
import json


urdf_allegro_path="./hand_model/allegro_hand_description/allegro_hand_description_right.urdf"
meshes_allegro_path="./hand_model/allegro_hand_description/meshes"
allegro_hand_model = HandModel("allegro", urdf_allegro_path, meshes_allegro_path, batch_size=1, device="cuda", hand_scale=1)

urdf_shadow_path="./hand_model/shadow_hand_description/urdf/shadowhand_adjust.urdf"
meshes_shadow_path="./hand_model/shadow_hand_description/meshes"
shadow_hand_model = HandModel("shadowhand", urdf_shadow_path, meshes_shadow_path, batch_size=1, device="cuda", hand_scale=1)


panda_gripper=PandaGripper()


urdf_barrett_path="./hand_model/barrett_hand_description/Barrett.urdf"
meshes_barrett_path="./hand_model/barrett_hand_description/meshes"
barrett_hand_model = HandModel("barrett", urdf_barrett_path, meshes_barrett_path, batch_size=1, device="cuda", hand_scale=1)

urdf_jaco_path="./hand_model/jaco_hand_description/jaco_robot.urdf"
meshes_jaco_path="./hand_model/jaco_hand_description/"
jaco_hand_model = HandModel("jaco", urdf_jaco_path, meshes_jaco_path, batch_size=1, device="cuda", hand_scale=1)

only got 89/128 samples!


only got 122/128 samples!
only got 124/128 samples!
only got 123/128 samples!
only got 125/128 samples!
only got 127/128 samples!
only got 121/128 samples!


Processing link #0: base_link
Processing link #1: link_0.0
Processing link #2: link_1.0
Processing link #3: link_2.0
Processing link #4: link_3.0
Processing link #5: link_3.0_tip
Processing link #6: link_4.0
Processing link #7: link_5.0
Processing link #8: link_6.0
Processing link #9: link_7.0
Processing link #10: link_7.0_tip
Processing link #11: link_8.0
Processing link #12: link_9.0
Processing link #13: link_10.0
Processing link #14: link_11.0
Processing link #15: link_11.0_tip
Processing link #16: link_12.0
Processing link #17: link_13.0
Processing link #18: link_14.0
Processing link #19: link_15.0
Processing link #20: link_15.0_tip
Processing link #0: palm


only got 58/64 samples!
only got 63/64 samples!
only got 62/64 samples!


Processing link #1: ffknuckle
Processing link #2: ffproximal
Processing link #3: ffmiddle
Processing link #4: ffdistal
Processing link #5: fftip
Processing link #6: mfknuckle
Processing link #7: mfproximal
Processing link #8: mfmiddle
Processing link #9: mfdistal
Processing link #10: mftip
Processing link #11: rfknuckle
Processing link #12: rfproximal
Processing link #13: rfmiddle
Processing link #14: rfdistal
Processing link #15: rftip
Processing link #16: lfmetacarpal
Processing link #17: lfknuckle
Processing link #18: lfproximal
Processing link #19: lfmiddle
Processing link #20: lfdistal
Processing link #21: lftip
Processing link #22: thbase
Processing link #23: thproximal
Processing link #24: thhub
Processing link #25: thmiddle


only got 126/128 samples!
only got 115/128 samples!
only got 124/128 samples!
only got 125/128 samples!
only got 122/128 samples!


Processing link #26: thdistal
Processing link #27: thtip
Processing link #0: base_link
Processing link #1: palm
Processing link #2: a_link1
Processing link #3: a_link2
Processing link #4: a_link3
Processing link #5: a_link1_joint
Processing link #6: a_link1_dh
Processing link #7: a_link2_joint
Processing link #8: a_link2_dh
Processing link #9: a_link3_joint
Processing link #10: a_link3_dh
Processing link #11: b_link1
Processing link #12: b_link2
Processing link #13: b_link3
Processing link #14: b_link1_joint
Processing link #15: b_link1_dh
Processing link #16: b_link2_joint
Processing link #17: b_link2_dh
Processing link #18: b_link3_joint
Processing link #19: b_link3_dh
Processing link #20: c_link2
Processing link #21: c_link3
Processing link #22: c_link2_joint
Processing link #23: c_link2_joint_0
Processing link #24: c_link2_dh
Processing link #25: c_link3_joint
Processing link #26: c_link3_dh
Processing link #0: base_link
Processing link #1: jaco_6_hand_limb
Processing link #2: jaco

In [8]:
import pickle

with open("./mid-level-data/shadow.pkl","rb") as f:
    meta_shadow=pickle.load(f)

with open("./mid-level-data/allegro.pkl","rb") as f:
    meta_allegro=pickle.load(f)
    
with open("./mid-level-data/panda.pkl","rb") as f:
    meta_panda=pickle.load(f)
    
with open("./mid-level-data/barrett.pkl","rb") as f:
    meta_barret=pickle.load(f)
    
with open("./mid-level-data/jaco.pkl","rb") as f:
    meta_jaco=pickle.load(f)    
    

# Visualize Allegro Hand

In [14]:
import trimesh
import re
import torch
import numpy as np
vocab_size=511
object_code="cylinder_bottle_s104"
num=0

angle=meta_allegro[object_code][num]['angle']
obj_id=object_code


infer_pose=torch.tensor(angle[0]+angle[1][:, :2].T.ravel().tolist()+angle[2])
mesh_hand_list_infer=allegro_hand_model.get_meshes_from_q(q=infer_pose.cuda().unsqueeze(0))
mesh_hand= trimesh.util.concatenate(mesh_hand_list_infer)

pc=np.load(f"./pc_8192/{obj_id}.npy")[:,:3]
point_colors = np.tile([255, 0, 0, 255], (pc.shape[0], 1))
point_cloud = trimesh.points.PointCloud(pc,colors=point_colors)
mesh_obj=trimesh.load(f"./Mesh_nor/{object_code}.obj",force="mesh")

print(meta_allegro[object_code][num]['contact_info'])
scene = trimesh.Scene()
scene.add_geometry(point_cloud)
# scene.add_geometry(mesh_obj)
scene.add_geometry(mesh_hand)

scene.show()

Middle finger,thumb finger and index finger touch the bottle body of cylinder_bottle,little finger touches the bottle cap of cylinder_bottle.


# Visualize Shadow Hand

In [12]:
import trimesh
import re
vocab_size=511
object_code="mug_s139"
num=1
angle=meta_shadow[object_code][num]['angle']
obj_id=object_code





infer_pose=torch.tensor(angle[0]+angle[1][:, :2].T.ravel().tolist()+angle[2])
mesh_hand_list_infer=shadow_hand_model.get_meshes_from_q(q=infer_pose.cuda().unsqueeze(0))
mesh_hand= trimesh.util.concatenate(mesh_hand_list_infer)

print(meta_shadow[object_code][num]['contact_info'])
pc=np.load(f"./pc_8192/{obj_id}.npy")[:,:3]
point_colors = np.tile([255, 0, 0, 255], (pc.shape[0], 1))
point_cloud = trimesh.points.PointCloud(pc,colors=point_colors)
scene = trimesh.Scene()
scene.add_geometry(point_cloud)
scene.add_geometry(mesh_hand)
scene.show()

['Little finger,ring finger,middle finger,thumb finger and index finger touch the mug body of mug.', 'all fingers touches the mug body of mug']


# Visual Panda Gripper

In [13]:
object_code="chaoneng_handwash"
print(meta_panda[object_code].keys())

angle=meta_panda[object_code]['pump head'][0]
mesh_hand=panda_gripper.get_meshes(angle)

pc=np.load(f"./pc_8192/{object_code}.npy")[:,:3]
point_colors = np.tile([255, 0, 0, 255], (pc.shape[0], 1))
point_cloud = trimesh.points.PointCloud(pc,colors=point_colors)
scene = trimesh.Scene()
scene.add_geometry(point_cloud)
scene.add_geometry(mesh_hand)
scene.show()

dict_keys(['pump head', 'bottle body'])


# Visualize Barrett

In [7]:
angle

([-0.014817648685191163, 0.115100027408388, -0.17385810370641025],
 array([[-0.0887277 ,  0.90763646,  0.41027241],
        [ 0.19694446,  0.41975144, -0.88601445],
        [-0.97639146,  0.00218686, -0.21599755]]),
 [0.820802, 0.813802, 1.05])

In [10]:
import trimesh
import re
import torch
import numpy as np
vocab_size=511
object_code="mug_s139"
num=0
angle=meta_barret[object_code][num]['angle']
obj_id=object_code





infer_pose=torch.tensor(angle[0]+angle[1][:, :2].T.ravel().tolist()+angle[2])
mesh_hand_list_infer=barrett_hand_model.get_meshes_from_q(q=infer_pose.cuda().unsqueeze(0))
mesh_hand= trimesh.util.concatenate(mesh_hand_list_infer)

print(meta_barret[object_code][num]['contact_info'])
pc=np.load(f"./pc_8192/{object_code}.npy")[:,:3]
point_colors = np.tile([255, 0, 0, 255], (pc.shape[0], 1))
point_cloud = trimesh.points.PointCloud(pc,colors=point_colors)
scene = trimesh.Scene()
scene.add_geometry(point_cloud)
scene.add_geometry(mesh_hand)
scene.show()

all fingers touches the mug body of mug


# Jaco

In [11]:
import trimesh
import re
import torch
import numpy as np
vocab_size=511
object_code="mug_s139"
num=0
angle=meta_jaco[object_code][num]['angle']
obj_id=object_code





infer_pose=torch.tensor(angle[0]+angle[1][:, :2].T.ravel().tolist()+angle[2])
mesh_hand_list_infer=jaco_hand_model.get_meshes_from_q(q=infer_pose.cuda().unsqueeze(0))
mesh_hand= trimesh.util.concatenate(mesh_hand_list_infer)

print(meta_jaco[object_code][num]['contact_info'])
pc=np.load(f"./pc_8192/{object_code}.npy")[:,:3]
point_colors = np.tile([255, 0, 0, 255], (pc.shape[0], 1))
point_cloud = trimesh.points.PointCloud(pc,colors=point_colors)
scene = trimesh.Scene()
scene.add_geometry(point_cloud)
scene.add_geometry(mesh_hand)
scene.show()

2 fingers touches the mug handle of mug
